In [1]:
import os
import requests
import tarfile
import csv
from bs4 import BeautifulSoup

In [2]:
# URL containing the .tgz files
BASE_URL = "http://www.repository.voxforge1.org/downloads/SpeechCorpus/Trunk/Audio/Main/16kHz_16bit/"
DOWNLOAD_DIR = "voxforge_wav_files"
ARCHIVE_DIR = "voxforge_archives"
CSV_FILE = "gender_labels.csv"

# Create directories if not exist
os.makedirs(DOWNLOAD_DIR, exist_ok=True)
os.makedirs(ARCHIVE_DIR, exist_ok=True)

In [3]:
# Function to get all .tgz file links from the page
def get_tgz_links():
    response = requests.get(BASE_URL)
    response.raise_for_status()
    soup = BeautifulSoup(response.text, "html.parser")
    
    tgz_links = []
    for link in soup.find_all("a"):
        href = link.get("href")
        if href and href.endswith(".tgz"):
            tgz_links.append(BASE_URL + href)
    
    return tgz_links

In [4]:
# Function to download a file
def download_file(url, save_path):
    response = requests.get(url, stream=True)
    response.raise_for_status()
    with open(save_path, "wb") as f:
        for chunk in response.iter_content(chunk_size=8192):
            f.write(chunk)
    print(f"Downloaded: {save_path}")

In [5]:
# Function to extract .wav files and README info
def extract_wav_and_metadata(tgz_path, extract_dir):
    gender = "Unknown"
    speaker_id = os.path.basename(tgz_path).replace(".tgz", "")
    wav_files = []

    with tarfile.open(tgz_path, "r:gz") as tar:
        for member in tar.getmembers():
            if member.name.endswith(".wav"):
                tar.extract(member, extract_dir)
                extracted_path = os.path.join(extract_dir, os.path.basename(member.name))
                wav_files.append(extracted_path)
                print(f"Extracted: {member.name}")

            elif "README" in member.name:
                f = tar.extractfile(member)
                if f:
                    content = f.read().decode("utf-8", errors="ignore")
                    gender = parse_gender(content)

    return speaker_id, gender, wav_files

In [6]:
# Function to parse gender from README file
def parse_gender(readme_text):
    readme_text = readme_text.lower()
    if "gender: male" in readme_text:
        return "male"
    elif "gender: female" in readme_text:
        return "female"
    return "unknown"

In [7]:
# Main script
def main():
    tgz_links = get_tgz_links()
    print(f"Found {len(tgz_links)} .tgz files.")

    with open(CSV_FILE, mode="w", newline="") as csv_file:
        writer = csv.writer(csv_file)
        writer.writerow(["speaker_id", "gender", "wav_file"])

        for tgz_url in tgz_links:
            tgz_filename = tgz_url.split("/")[-1]
            tgz_path = os.path.join(ARCHIVE_DIR, tgz_filename)

            # Download if not already present
            if not os.path.exists(tgz_path):
                download_file(tgz_url, tgz_path)

            # Extract .wav files and metadata
            speaker_id, gender, wav_files = extract_wav_and_metadata(tgz_path, DOWNLOAD_DIR)

            # Save gender info for each wav file
            for wav_file in wav_files:
                writer.writerow([speaker_id, gender, wav_file])

    print(f"Metadata saved to {CSV_FILE}")

In [8]:
if __name__ == "__main__":
    main()

Found 6321 .tgz files.
Downloaded: voxforge_archives\1028-20100710-hne.tgz
Extracted: 1028-20100710-hne/wav/ar-05.wav
Extracted: 1028-20100710-hne/wav/ar-01.wav
Extracted: 1028-20100710-hne/wav/ar-07.wav
Extracted: 1028-20100710-hne/wav/ar-02.wav
Extracted: 1028-20100710-hne/wav/rp-29.wav
Extracted: 1028-20100710-hne/wav/ar-03.wav
Extracted: 1028-20100710-hne/wav/rp-30.wav
Extracted: 1028-20100710-hne/wav/ar-06.wav
Extracted: 1028-20100710-hne/wav/rp-31.wav
Extracted: 1028-20100710-hne/wav/ar-04.wav
Downloaded: voxforge_archives\1337ad-20170321-ajg.tgz
Extracted: 1337ad-20170321-ajg/wav/en-0533.wav
Extracted: 1337ad-20170321-ajg/wav/en-0538.wav
Extracted: 1337ad-20170321-ajg/wav/en-0534.wav
Extracted: 1337ad-20170321-ajg/wav/en-0540.wav
Extracted: 1337ad-20170321-ajg/wav/en-0539.wav
Extracted: 1337ad-20170321-ajg/wav/en-0532.wav
Extracted: 1337ad-20170321-ajg/wav/en-0535.wav
Extracted: 1337ad-20170321-ajg/wav/en-0537.wav
Extracted: 1337ad-20170321-ajg/wav/en-0541.wav
Extracted: 1337ad-

Downloaded: voxforge_archives\Aaron-20130527-giy.tgz
Extracted: Aaron-20130527-giy/wav/b0355.wav
Extracted: Aaron-20130527-giy/wav/b0358.wav
Extracted: Aaron-20130527-giy/wav/b0351.wav
Extracted: Aaron-20130527-giy/wav/b0359.wav
Extracted: Aaron-20130527-giy/wav/b0354.wav
Extracted: Aaron-20130527-giy/wav/b0352.wav
Extracted: Aaron-20130527-giy/wav/b0357.wav
Extracted: Aaron-20130527-giy/wav/b0350.wav
Extracted: Aaron-20130527-giy/wav/b0353.wav
Extracted: Aaron-20130527-giy/wav/b0356.wav
Downloaded: voxforge_archives\AbdulMoiz-20121010-juf.tgz
Extracted: AbdulMoiz-20121010-juf/wav/a0295.wav
Extracted: AbdulMoiz-20121010-juf/wav/a0286.wav
Extracted: AbdulMoiz-20121010-juf/wav/a0287.wav
Extracted: AbdulMoiz-20121010-juf/wav/a0289.wav
Extracted: AbdulMoiz-20121010-juf/wav/a0292.wav
Extracted: AbdulMoiz-20121010-juf/wav/a0293.wav
Extracted: AbdulMoiz-20121010-juf/wav/a0290.wav
Extracted: AbdulMoiz-20121010-juf/wav/a0291.wav
Extracted: AbdulMoiz-20121010-juf/wav/a0288.wav
Extracted: AbdulMo

Downloaded: voxforge_archives\AlexanderHenningDrachmann-20140108-klh.tgz
Extracted: AlexanderHenningDrachmann-20140108-klh/wav/a0403.wav
Extracted: AlexanderHenningDrachmann-20140108-klh/wav/a0404.wav
Extracted: AlexanderHenningDrachmann-20140108-klh/wav/a0405.wav
Extracted: AlexanderHenningDrachmann-20140108-klh/wav/a0399.wav
Extracted: AlexanderHenningDrachmann-20140108-klh/wav/a0407.wav
Extracted: AlexanderHenningDrachmann-20140108-klh/wav/a0402.wav
Extracted: AlexanderHenningDrachmann-20140108-klh/wav/a0406.wav
Extracted: AlexanderHenningDrachmann-20140108-klh/wav/a0401.wav
Extracted: AlexanderHenningDrachmann-20140108-klh/wav/a0400.wav
Extracted: AlexanderHenningDrachmann-20140108-klh/wav/a0398.wav
Downloaded: voxforge_archives\AlexanderHenningDrachmann-20140108-koe.tgz
Extracted: AlexanderHenningDrachmann-20140108-koe/wav/b0461.wav
Extracted: AlexanderHenningDrachmann-20140108-koe/wav/b0459.wav
Extracted: AlexanderHenningDrachmann-20140108-koe/wav/b0458.wav
Extracted: AlexanderHe

Downloaded: voxforge_archives\AndreyBarrientosCostaRica-20130720-pxz.tgz
Extracted: AndreyBarrientosCostaRica-20130720-pxz/wav/a0431.wav
Extracted: AndreyBarrientosCostaRica-20130720-pxz/wav/a0428.wav
Extracted: AndreyBarrientosCostaRica-20130720-pxz/wav/a0437.wav
Extracted: AndreyBarrientosCostaRica-20130720-pxz/wav/a0436.wav
Extracted: AndreyBarrientosCostaRica-20130720-pxz/wav/a0434.wav
Extracted: AndreyBarrientosCostaRica-20130720-pxz/wav/a0433.wav
Extracted: AndreyBarrientosCostaRica-20130720-pxz/wav/a0429.wav
Extracted: AndreyBarrientosCostaRica-20130720-pxz/wav/a0435.wav
Extracted: AndreyBarrientosCostaRica-20130720-pxz/wav/a0432.wav
Extracted: AndreyBarrientosCostaRica-20130720-pxz/wav/a0430.wav
Downloaded: voxforge_archives\Andy212380-20141016-lzl.tgz
Extracted: Andy212380-20141016-lzl/wav/b0531.wav
Extracted: Andy212380-20141016-lzl/wav/b0532.wav
Extracted: Andy212380-20141016-lzl/wav/b0535.wav
Extracted: Andy212380-20141016-lzl/wav/b0534.wav
Extracted: Andy212380-20141016-lz

Downloaded: voxforge_archives\Ara-20091020-vni.tgz
Extracted: Ara-20091020-vni/wav/a0519.wav
Extracted: Ara-20091020-vni/wav/a0524.wav
Extracted: Ara-20091020-vni/wav/a0521.wav
Extracted: Ara-20091020-vni/wav/a0522.wav
Extracted: Ara-20091020-vni/wav/a0520.wav
Extracted: Ara-20091020-vni/wav/a0525.wav
Extracted: Ara-20091020-vni/wav/a0518.wav
Extracted: Ara-20091020-vni/wav/a0517.wav
Extracted: Ara-20091020-vni/wav/a0523.wav
Extracted: Ara-20091020-vni/wav/a0526.wav
Downloaded: voxforge_archives\Ara-20091021-wpl.tgz
Extracted: Ara-20091021-wpl/wav/ar-24.wav
Extracted: Ara-20091021-wpl/wav/ar-20.wav
Extracted: Ara-20091021-wpl/wav/ar-16.wav
Extracted: Ara-20091021-wpl/wav/ar-18.wav
Extracted: Ara-20091021-wpl/wav/ar-19.wav
Extracted: Ara-20091021-wpl/wav/ar-23.wav
Extracted: Ara-20091021-wpl/wav/ar-22.wav
Extracted: Ara-20091021-wpl/wav/rb-01.wav
Extracted: Ara-20091021-wpl/wav/ar-21.wav
Extracted: Ara-20091021-wpl/wav/ar-17.wav
Downloaded: voxforge_archives\Artem-20121123-ebd.tgz
Extra

...

Downloaded: voxforge_archives\wesjackson-20130502-yeo.tgz
Extracted: wesjackson-20130502-yeo/wav/a0538.wav
Extracted: wesjackson-20130502-yeo/wav/a0542.wav
Extracted: wesjackson-20130502-yeo/wav/a0543.wav
Extracted: wesjackson-20130502-yeo/wav/a0547.wav
Extracted: wesjackson-20130502-yeo/wav/a0541.wav
Extracted: wesjackson-20130502-yeo/wav/a0539.wav
Extracted: wesjackson-20130502-yeo/wav/a0545.wav
Extracted: wesjackson-20130502-yeo/wav/a0544.wav
Extracted: wesjackson-20130502-yeo/wav/a0540.wav
Extracted: wesjackson-20130502-yeo/wav/a0546.wav
Downloaded: voxforge_archives\whappy-20090617-ltq.tgz
Extracted: whappy-20090617-ltq/wav/a0156.wav
Extracted: whappy-20090617-ltq/wav/a0159.wav
Extracted: whappy-20090617-ltq/wav/a0155.wav
Extracted: whappy-20090617-ltq/wav/a0158.wav
Extracted: whappy-20090617-ltq/wav/a0161.wav
Extracted: whappy-20090617-ltq/wav/a0160.wav
Extracted: whappy-20090617-ltq/wav/a0153.wav
Extracted: whappy-20090617-ltq/wav/a0157.wav
Extracted: whappy-20090617-ltq/wav/a01

Downloaded: voxforge_archives\wicke-20090314-jtl.tgz
Extracted: wicke-20090314-jtl/wav/rb-19.wav
Extracted: wicke-20090314-jtl/wav/rb-25.wav
Extracted: wicke-20090314-jtl/wav/rb-24.wav
Extracted: wicke-20090314-jtl/wav/rb-21.wav
Extracted: wicke-20090314-jtl/wav/rb-22.wav
Extracted: wicke-20090314-jtl/wav/rb-27.wav
Extracted: wicke-20090314-jtl/wav/rb-23.wav
Extracted: wicke-20090314-jtl/wav/rb-18.wav
Extracted: wicke-20090314-jtl/wav/rb-20.wav
Extracted: wicke-20090314-jtl/wav/rb-26.wav
Downloaded: voxforge_archives\wicke-20090314-jzq.tgz
Extracted: wicke-20090314-jzq/wav/b0141.wav
Extracted: wicke-20090314-jzq/wav/b0136.wav
Extracted: wicke-20090314-jzq/wav/b0144.wav
Extracted: wicke-20090314-jzq/wav/b0137.wav
Extracted: wicke-20090314-jzq/wav/b0138.wav
Extracted: wicke-20090314-jzq/wav/b0143.wav
Extracted: wicke-20090314-jzq/wav/b0140.wav
Extracted: wicke-20090314-jzq/wav/b0142.wav
Extracted: wicke-20090314-jzq/wav/b0145.wav
Extracted: wicke-20090314-jzq/wav/b0139.wav
Downloaded: vo

Downloaded: voxforge_archives\xh-20100802-aed.tgz
Extracted: xh-20100802-aed/wav/b0421.wav
Extracted: xh-20100802-aed/wav/b0420.wav
Extracted: xh-20100802-aed/wav/b0423.wav
Extracted: xh-20100802-aed/wav/b0422.wav
Extracted: xh-20100802-aed/wav/b0427.wav
Extracted: xh-20100802-aed/wav/b0426.wav
Extracted: xh-20100802-aed/wav/b0424.wav
Extracted: xh-20100802-aed/wav/b0429.wav
Extracted: xh-20100802-aed/wav/b0425.wav
Extracted: xh-20100802-aed/wav/b0428.wav
Downloaded: voxforge_archives\xh-20100802-cht.tgz
Extracted: xh-20100802-cht/wav/b0136.wav
Extracted: xh-20100802-cht/wav/b0138.wav
Extracted: xh-20100802-cht/wav/b0132.wav
Extracted: xh-20100802-cht/wav/b0135.wav
Extracted: xh-20100802-cht/wav/b0133.wav
Extracted: xh-20100802-cht/wav/b0137.wav
Extracted: xh-20100802-cht/wav/b0134.wav
Extracted: xh-20100802-cht/wav/b0129.wav
Downloaded: voxforge_archives\xh-20100802-dvc.tgz
Extracted: xh-20100802-dvc/wav/b0266.wav
Extracted: xh-20100802-dvc/wav/b0259.wav
Extracted: xh-20100802-dvc/wav

Downloaded: voxforge_archives\xtophe-20080924-ulu.tgz
Extracted: xtophe-20080924-ulu/wav/b0188.wav
Extracted: xtophe-20080924-ulu/wav/b0193.wav
Extracted: xtophe-20080924-ulu/wav/b0190.wav
Extracted: xtophe-20080924-ulu/wav/b0192.wav
Extracted: xtophe-20080924-ulu/wav/b0186.wav
Extracted: xtophe-20080924-ulu/wav/b0189.wav
Extracted: xtophe-20080924-ulu/wav/b0187.wav
Extracted: xtophe-20080924-ulu/wav/b0191.wav
Extracted: xtophe-20080924-ulu/wav/b0184.wav
Extracted: xtophe-20080924-ulu/wav/b0185.wav
Downloaded: voxforge_archives\xtophe-20080924-wcq.tgz
Extracted: xtophe-20080924-wcq/wav/a0194.wav
Extracted: xtophe-20080924-wcq/wav/a0191.wav
Extracted: xtophe-20080924-wcq/wav/a0193.wav
Extracted: xtophe-20080924-wcq/wav/a0192.wav
Extracted: xtophe-20080924-wcq/wav/a0195.wav
Extracted: xtophe-20080924-wcq/wav/a0189.wav
Extracted: xtophe-20080924-wcq/wav/a0196.wav
Extracted: xtophe-20080924-wcq/wav/a0190.wav
Extracted: xtophe-20080924-wcq/wav/a0197.wav
Extracted: xtophe-20080924-wcq/wav/a0

Downloaded: voxforge_archives\zeroschism-20160710.tgz
Extracted: zeroschism-20160710/wav/cc-26.wav
Extracted: zeroschism-20160710/wav/cc-34.wav
Extracted: zeroschism-20160710/wav/cc-15.wav
Extracted: zeroschism-20160710/wav/cc-01.wav
Extracted: zeroschism-20160710/wav/cc-16.wav
Extracted: zeroschism-20160710/wav/cc-38.wav
Extracted: zeroschism-20160710/wav/cc-18.wav
Extracted: zeroschism-20160710/wav/cc-09.wav
Extracted: zeroschism-20160710/wav/cc-03.wav
Extracted: zeroschism-20160710/wav/cc-31.wav
Extracted: zeroschism-20160710/wav/cc-36.wav
Extracted: zeroschism-20160710/wav/cc-19.wav
Extracted: zeroschism-20160710/wav/cc-05.wav
Extracted: zeroschism-20160710/wav/cc-02.wav
Extracted: zeroschism-20160710/wav/cc-10.wav
Extracted: zeroschism-20160710/wav/cc-32.wav
Extracted: zeroschism-20160710/wav/cc-06.wav
Extracted: zeroschism-20160710/wav/cc-11.wav
Extracted: zeroschism-20160710/wav/cc-12.wav
Extracted: zeroschism-20160710/wav/cc-14.wav
Extracted: zeroschism-20160710/wav/cc-35.wav
E